In [1]:
from imutils import face_utils
import numpy as np
import imutils
import dlib
import cv2
import sys
sys.path.append( 'SAN' )
import san_eval

In [2]:
# load file
FILE_NAME = "00485_Chinese_Asian_Female_Young/00485_1"
# define video path
VIDEOPATH = "video/" + FILE_NAME + ".mp4"
# define json path
JSONPATH = "video/" + FILE_NAME + ".json"
# define lip region
(LIPFROM, LIPTO) = (48, 68)
# define threshold for lip motion
HIGH_THRESHOLD = 0.65
LOW_THRESHOLD = 0.4

# define the face detector
DETECTOR = dlib.get_frontal_face_detector()

# read original video
# fvs = FileVideoStream(path=VIDEOPATH).start()
VC = cv2.VideoCapture(VIDEOPATH)
FRAME_RATE = VC.get(cv2.CAP_PROP_FPS)
# define output video
FRAME_WIDTH = int(VC.get(cv2.CAP_PROP_FRAME_WIDTH))
FRAME_HEIGHT = int(VC.get(cv2.CAP_PROP_FRAME_HEIGHT))

In [3]:
def lip_aspect_ratio(lip):

    # left top to left bottom
    A = np.linalg.norm(lip[2] - lip[9])  # 51, 59
    # right top to right bottom
    B = np.linalg.norm(lip[4] - lip[7])  # 53, 57
    # leftest to rightest
    C = np.linalg.norm(lip[0] - lip[6])  # 49, 55
    lar = (A + B) / (2.0 * C)

    return lar

In [4]:
class Args():
    def __init__(self, image, face, save_path=None, cpu=False):
        self.image = image
        self.model = 'SAN/snapshots/SAN_300W_GTB_itn_cpm_3_50_sigma4_128x128x8/checkpoint_49.pth.tar'
        self.face = face
        self.save_path = save_path
        self.cpu = cpu

In [8]:
LARs = []
count = 1
while (VC.isOpened()):
    # read frames
    rval, frame = VC.read()
    if rval:
        cv2.imwrite('frame.jpg', frame)
        frame_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        rects = DETECTOR(frame_rgb, 0)
        if len(rects) == 0:
            print('Fail to find a face!')
            LARs.append(0)
        else:
            rect = rects[0]
            left = rect.tl_corner().x
            top = rect.tl_corner().y
            right = rect.br_corner().x
            bottom = rect.br_corner().y
            face = [left, top, right, bottom]
            args = Args('frame.jpg', face)
            shape = san_eval.evaluate(args)
            shape = np.array(shape)
            # locate lip region
            lip = shape[LIPFROM:LIPTO]
            # get lip aspect ratio
            lar = lip_aspect_ratio(lip)
            LARs.append(lar)
        count += 1
        if count % 200 == 0:
            break
    else:
        break


VC.release()

The image is frame.jpg
The model is SAN/snapshots/SAN_300W_GTB_itn_cpm_3_50_sigma4_128x128x8/checkpoint_49.pth.tar
The face bounding box is [156, 569, 527, 940]
Initialize ITN-CPM with configure : ModelConfig(points=69, stage=3, PreTrain=True, ArgMax=3)
vgg16_base use pre-trained model
==>[load_model] finetuned layers : ['features.0.weight', 'features.0.bias', 'features.2.weight', 'features.2.bias', 'features.5.weight', 'features.5.bias', 'features.7.weight', 'features.7.bias', 'features.10.weight', 'features.10.bias', 'features.12.weight', 'features.12.bias', 'features.14.weight', 'features.14.bias', 'features.17.weight', 'features.17.bias', 'features.19.weight', 'features.19.bias', 'features.21.weight', 'features.21.bias']
==>[load_model] keeped layers : ['netG_A.model.1.weight', 'netG_A.model.1.bias', 'netG_A.model.4.weight', 'netG_A.model.4.bias', 'netG_A.model.7.weight', 'netG_A.model.7.bias', 'netG_A.model.10.conv_block.1.weight', 'netG_A.model.10.conv_block.1.bias', 'netG_A.mode

In [9]:
print(LARs)

[0.6752559884442791, 0.6463471097522548, 0.6536421729655498, 0.6827876641099535, 0.6585846738079483, 0.6434097972412042, 0.631750738685347, 0.6284446965742313, 0.6246508542844448, 0.6338285292551674, 0.6440994698454742, 0.6596174229854355, 0.6611525102803274, 0.6140263662676094, 0.6005611823239615, 0.6013365122677957, 0.5950588324076489, 0.6045567589874178, 0.6147525304879804, 0.5907879341715717, 0.585873528588886, 0.5701721331069803, 0.5769567700545997, 0.5612635886900583, 0.5590980260989643, 0.563523980637195, 0.5752712950242992, 0.5589321846405201, 0.5589321846405201, 0.5601116003873634, 0.5362328787072109, 0.559911698390514, 0.5509424278053868, 0.539715742536356, 0.5445229399568094, 0.5550190901727698, 0.5550190901727698, 0.559911698390514, 0.5425078920743502, 0.5972367569838912, 0.5894558292397339, 0.617145613847156, 0.614168106705194, 0.6212243818227338, 0.6158659166723551, 0.6151341092992112, 0.6245372492916197, 0.6215851478967045, 0.6431196942844081, 0.6333004911402009, 0.63028